In [ ]:
import os
import cv2
import numpy as np
from ultralytics import YOLO
from tqdm import tqdm

# Ruta base donde se encuentran los datos
base_path = r'C:\Users\Invitado\Documents\facial_expression_detector\data_procesada\data\SUJETO 4\señas_procesadas'

# Cargar el modelo YOLO11
model = YOLO('yolo11n.pt')  # Usar el modelo YOLOv11 nano

# Tamaño objetivo para normalizar
target_height = 640
target_width = 640

def process_image(input_path, output_path):
    """
    Procesa una imagen usando YOLO para detectar personas,
    recorta la región de interés y la normaliza
    
    Args:
        input_path: Ruta de la imagen de entrada
        output_path: Ruta donde guardar la imagen procesada
    
    Returns:
        bool: True si se procesó correctamente, False en caso contrario
    """
    try:
        # Leer imagen compatible con rutas con tildes/ñ
        img_data = np.fromfile(input_path, dtype=np.uint8)
        image = cv2.imdecode(img_data, cv2.IMREAD_COLOR)

        if image is None:
            print(f"❌ Imagen no leída: {input_path}")
            return False

        # Usar YOLO11 para detectar personas
        results = model(image)
        
        max_area = 0
        best_box = None
        
        # Iterar sobre los resultados de la detección
        for r in results:
            for box in r.boxes:
                if int(box.cls[0]) == 0:  # Clase 'persona' (generalmente 0 en YOLO)
                    x1, y1, x2, y2 = map(int, box.xyxy[0])
                    area = (x2 - x1) * (y2 - y1)  # Calcular área del bounding box
                    if area > max_area:
                        max_area = area
                        best_box = (x1, y1, x2, y2)

        # Si encontramos el bounding box con la mayor área, recortamos la imagen
        if best_box:
            x1, y1, x2, y2 = best_box
            
            # Ajustar el recorte para enfocarse en el pecho y la cabeza
            # Vamos a incrementar un poco el área hacia arriba, eliminando la cintura
            y1 = max(y1 - int((y2 - y1) * 0.2), 0)  # Aumentar el área hacia arriba (20% del alto del box)
            y2 = y1 + int((y2 - y1) * 0.85)  # Limitar el recorte a la cabeza

            cropped = image[y1:y2, x1:x2]  # Recortar la imagen en base al bounding box ajustado

            # Normalizar la imagen sin distorsionar
            cropped_h, cropped_w = cropped.shape[:2]

            # Redimensionar la imagen para que sea el tamaño objetivo
            resized = cv2.resize(cropped, (target_width, target_height), interpolation=cv2.INTER_LINEAR)

            # Crear directorio de salida si no existe
            os.makedirs(os.path.dirname(output_path), exist_ok=True)
            
            # Guardar la imagen recortada y normalizada
            cv2.imwrite(output_path, resized)
            return True
        else:
            print(f"❌ No se detectó ninguna persona en la imagen: {input_path}")
            return False
            
    except Exception as e:
        print(f"❌ Error procesando {input_path}: {e}")
        return False

def process_rgb_folder(input_folder, output_folder):
    """
    Procesa todas las imágenes de una carpeta rgb
    
    Args:
        input_folder: Ruta de la carpeta con las imágenes originales
        output_folder: Ruta donde guardar las imágenes procesadas
    
    Returns:
        tuple: (total_images, processed_images)
    """
    # Asegurarse de que la carpeta de salida existe
    os.makedirs(output_folder, exist_ok=True)
    
    # Obtener todas las imágenes en la carpeta, ordenadas
    image_files = sorted([f for f in os.listdir(input_folder) 
                      if f.lower().endswith(('.jpg', '.jpeg', '.png'))])
    
    if not image_files:
        print(f"❌ No se encontraron imágenes en la carpeta: {input_folder}")
        return 0, 0
    
    processed_count = 0
    
    # Procesar cada imagen
    for filename in tqdm(image_files, desc=f"Procesando {os.path.basename(input_folder)}"):
        input_path = os.path.join(input_folder, filename)
        output_path = os.path.join(output_folder, filename)
        
        if process_image(input_path, output_path):
            processed_count += 1
    
    return len(image_files), processed_count

def process_all_a_ver_folders():
    """
    Recorre todas las carpetas 'A ver' dentro de la estructura y procesa las imágenes RGB
    """
    # Construir la ruta base para 'A ver'
    a_ver_base = os.path.join(base_path, 'A ver')
    
    # Verificar si la carpeta existe
    if not os.path.exists(a_ver_base):
        print(f"❌ La carpeta 'A ver' no existe en: {base_path}")
        return
    
    # Obtener todas las subcarpetas 'muestra_X'
    muestra_folders = [f for f in os.listdir(a_ver_base) if f.startswith('muestra_')]
    
    if not muestra_folders:
        print(f"❌ No se encontraron carpetas 'muestra_X' en: {a_ver_base}")
        return
    
    total_samples = 0
    total_processed = 0
    
    # Procesar cada carpeta muestra
    for muestra_folder in muestra_folders:
        muestra_path = os.path.join(a_ver_base, muestra_folder)
        
        # Buscar la carpeta 'rgb' dentro de cada muestra
        rgb_path = os.path.join(muestra_path, 'rgb')
        
        if os.path.exists(rgb_path) and os.path.isdir(rgb_path):
            # Crear carpeta de recortes
            recortes_path = os.path.join(muestra_path, 'recortes')
            
            print(f"\n🔍 Procesando: A ver/{muestra_folder}/rgb")
            samples, processed = process_rgb_folder(rgb_path, recortes_path)
            
            total_samples += samples
            total_processed += processed
            
            print(f"✅ Procesadas {processed}/{samples} imágenes en A ver/{muestra_folder}")
        else:
            print(f"⚠️ No se encontró la carpeta 'rgb' en: {muestra_path}")
    
    print(f"\n✅ Proceso completado. {total_processed}/{total_samples} imágenes procesadas en 'A ver'")

def process_all_expressions():
    """
    Recorre todas las carpetas de expresiones (incluyendo 'A ver', 'Feliz', etc.)
    y procesa las imágenes RGB
    """
    # Obtener todas las carpetas de expresiones
    expression_folders = [f for f in os.listdir(base_path) if os.path.isdir(os.path.join(base_path, f))]
    
    if not expression_folders:
        print(f"❌ No se encontraron carpetas de expresiones en: {base_path}")
        return
    
    total_samples = 0
    total_processed = 0
    
    # Procesar cada carpeta de expresión
    for expression in expression_folders:
        expression_path = os.path.join(base_path, expression)
        print(f"\n🔍 Procesando expresión: {expression}")
        
        expression_samples = 0
        expression_processed = 0
        
        # Obtener todas las subcarpetas 'muestra_X'
        try:
            muestra_folders = [f for f in os.listdir(expression_path) if f.startswith('muestra_')]
        except Exception as e:
            print(f"❌ Error al listar carpetas en {expression_path}: {e}")
            continue
        
        for muestra_folder in muestra_folders:
            muestra_path = os.path.join(expression_path, muestra_folder)
            
            # Buscar la carpeta 'rgb' dentro de cada muestra
            rgb_path = os.path.join(muestra_path, 'rgb')
            
            if os.path.exists(rgb_path) and os.path.isdir(rgb_path):
                # Crear carpeta de recortes
                recortes_path = os.path.join(muestra_path, 'recortes')
                
                print(f"\n🔍 Procesando: {expression}/{muestra_folder}/rgb")
                samples, processed = process_rgb_folder(rgb_path, recortes_path)
                
                expression_samples += samples
                expression_processed += processed
                
                print(f"✅ Procesadas {processed}/{samples} imágenes en {expression}/{muestra_folder}")
            else:
                print(f"⚠️ No se encontró la carpeta 'rgb' en: {muestra_path}")
        
        total_samples += expression_samples
        total_processed += expression_processed
        
        print(f"📊 Expresión '{expression}': {expression_processed}/{expression_samples} imágenes procesadas")
    
    print(f"\n✅ Proceso completado. Total: {total_processed}/{total_samples} imágenes procesadas")

# Menú principal
if __name__ == "__main__":
    print("===== PROCESADOR DE IMÁGENES CON YOLO =====")
    print("Este script detectará personas en las imágenes, recortará")
    print("la región de interés (cabeza y pecho) y normalizará el tamaño.")
    print(f"Se usará el modelo YOLOv11 nano para la detección.\n")
    
    print("¿Qué deseas procesar?")
    print("1. Solo las carpetas de 'A ver'")
    print("2. Todas las expresiones (incluyendo 'A ver' y otras)")
    
    choice = input("\nIngresa tu opción (1 o 2): ")
    
    if choice == "1":
        print("\nProcesando solo las carpetas de 'A ver'...\n")
        process_all_a_ver_folders()
    elif choice == "2":
        print("\nProcesando todas las expresiones...\n")
        process_all_expressions()
    else:
        print("❌ Opción inválida. Saliendo.")

RECORTE DE ROSTRO

In [16]:
import os
import cv2
import numpy as np
from ultralytics import YOLO
from tqdm import tqdm

# Cargar el modelo YOLO11
model = YOLO('yolo11n.pt')  # Usar el modelo YOLOv11 nano

# Tamaño objetivo para normalizar manteniendo proporción
target_size = 640

def process_image(input_path, output_path):
    """
    Procesa una imagen usando YOLO para detectar personas,
    recorta la región de interés enfocada solo en el rostro
    y normaliza sin deformar
    
    Args:
        input_path: Ruta de la imagen de entrada
        output_path: Ruta donde guardar la imagen procesada
    
    Returns:
        bool: True si se procesó correctamente, False en caso contrario
    """
    try:
        # Leer imagen compatible con rutas con tildes/ñ y espacios
        try:
            # Primero intentar lectura directa
            image = cv2.imread(input_path)
            
            # Si falla, usar el método alternativo con numpy
            if image is None:
                img_data = np.fromfile(input_path, dtype=np.uint8)
                image = cv2.imdecode(img_data, cv2.IMREAD_COLOR)
        except Exception as e:
            print(f"❌ Error leyendo imagen {input_path}: {e}")
            return False

        if image is None:
            print(f"❌ Imagen no leída: {input_path}")
            return False
            
        # Detectar y eliminar barras negras horizontales
        height, width = image.shape[:2]
        
        # Buscar filas completamente negras o casi negras (umbral bajo)
        threshold = 10  # Umbral para considerar un pixel como "negro"
        
        # Analizar la parte superior
        top_crop = 0
        for i in range(height // 2):  # Solo analizamos la mitad superior
            row_avg = np.mean(image[i])
            if row_avg > threshold:
                top_crop = i
                break
                
        # Analizar la parte inferior
        bottom_crop = height - 1
        for i in range(height - 1, height // 2, -1):  # Solo analizamos la mitad inferior
            row_avg = np.mean(image[i])
            if row_avg > threshold:
                bottom_crop = i
                break
                
        # Recortar la imagen para eliminar barras negras
        if top_crop > 0 or bottom_crop < height - 1:
            image = image[top_crop:bottom_crop+1, :]

        # Usar YOLO11 para detectar personas
        results = model(image)
        
        max_area = 0
        best_box = None
        
        # Iterar sobre los resultados de la detección
        for r in results:
            for box in r.boxes:
                if int(box.cls[0]) == 0:  # Clase 'persona' (generalmente 0 en YOLO)
                    x1, y1, x2, y2 = map(int, box.xyxy[0])
                    area = (x2 - x1) * (y2 - y1)  # Calcular área del bounding box
                    if area > max_area:
                        max_area = area
                        best_box = (x1, y1, x2, y2)

        # Si encontramos el bounding box con la mayor área, recortamos la imagen
        if best_box:
            x1, y1, x2, y2 = best_box
            
            # Calcular proporciones basadas en la altura total de la persona
            box_height = y2 - y1
            
            # Para estimar mejor la posición de la cabeza, usamos la quinta parte superior del bounding box
            head_region_height = box_height / 5
            
            # Convertir a entero para evitar el error de índice
            head_region_height = int(head_region_height)
            
            # Estimamos que la cara está aproximadamente en la parte superior
            face_y = y1 + head_region_height // 2
            
            # SOLUCIÓN: Corrección para asegurar que el rostro completo sea visible
            # Estimamos posición del rostro en una ubicación mucho más alta
            # basado en la quinta parte superior del bounding box
            
            # Calculamos un valor aproximado para la ubicación del rostro
            # Usando un porcentaje menor del altura total para ubicar el rostro más arriba
            face_y_center = y1 + int(box_height * 0.1)  # Posicionamos el centro mucho más arriba
            
            # Dimensión vertical para el recorte - aseguramos capturar suficiente del rostro
            face_height = int(box_height * 0.2)  # 20% de la altura total
            
            # Calcular los puntos de recorte - asegurarnos que son enteros
            # Ampliamos la región para asegurar que captura el rostro completo
            new_y1 = max(int(face_y_center - face_height/2), 0)
            new_y2 = min(int(face_y_center + face_height), image.shape[0])
            
            # Centro horizontal del rostro - usamos el centro del bounding box
            face_center_x = (x1 + x2) // 2
            
            # Usamos un factor de ancho proporcional para asegurar capturar el rostro completo
            # Sin recortar lateralmente
            width_factor = 1  # Factor para asegurar que todo el rostro sea visible
            
            # Calculamos márgenes laterales proporcionales a la altura
            face_width = int((new_y2 - new_y1) * width_factor)
            
            # Calculamos los límites horizontales centrados en la cara
            new_x1 = max(int(face_center_x - face_width/2), 0)
            new_x2 = min(int(face_center_x + face_width/2), image.shape[1])
            
            # Recortar la imagen en base a los nuevos límites calculados
            cropped = image[new_y1:new_y2, new_x1:new_x2]
            
            # CAMBIO: Evitamos generar un lienzo negro y simplemente redimensionamos
            # directamente para evitar los bordes negros
            
            # Redimensionar directamente al tamaño objetivo
            resized = cv2.resize(cropped, (target_size, target_size), interpolation=cv2.INTER_AREA)

            # Crear directorio de salida si no existe
            os.makedirs(os.path.dirname(output_path), exist_ok=True)
            
            # Guardar la imagen procesada usando el método de codificación para manejar rutas con espacios
            try:
                # Intentar guardar directamente primero
                success = cv2.imwrite(output_path, resized)
                
                # Si falla, usar el método alternativo
                if not success:
                    _, buffer = cv2.imencode('.png', resized)
                    with open(output_path, 'wb') as f:
                        f.write(buffer)
            except Exception as e:
                print(f"❌ Error guardando la imagen {output_path}: {e}")
                return False
                
            return True
        else:
            print(f"❌ No se detectó ninguna persona en la imagen: {input_path}")
            return False
            
    except Exception as e:
        print(f"❌ Error procesando {input_path}: {e}")
        import traceback
        traceback.print_exc()  # Imprimir el stack trace completo para mejor diagnóstico
        return False

def process_folder(input_folder, output_folder, recursive=True):
    """
    Procesa todas las imágenes de una carpeta
    
    Args:
        input_folder: Ruta de la carpeta con las imágenes originales
        output_folder: Ruta donde guardar las imágenes procesadas
        recursive: Si debe procesarse recursivamente las subcarpetas
    
    Returns:
        tuple: (total_images, processed_images)
    """
    try:
        # Asegurarse de que la carpeta de salida existe
        os.makedirs(output_folder, exist_ok=True)
        
        total_images = 0
        processed_images = 0
        
        # Si el modo es recursivo, procesar todas las subcarpetas
        if recursive:
            for root, dirs, files in os.walk(input_folder):
                # Crear la estructura de carpetas correspondiente en la carpeta de salida
                rel_path = os.path.relpath(root, input_folder)
                if rel_path == '.':
                    current_output_folder = output_folder
                else:
                    current_output_folder = os.path.join(output_folder, rel_path)
                    os.makedirs(current_output_folder, exist_ok=True)
                
                # Filtrar solo archivos de imagen
                image_files = [f for f in files if f.lower().endswith(('.jpg', '.jpeg', '.png'))]
                
                if image_files:
                    print(f"\n🔍 Procesando: {rel_path}")
                    
                    for filename in tqdm(image_files, desc=f"Procesando {os.path.basename(root)}"):
                        input_path = os.path.join(root, filename)
                        output_path = os.path.join(current_output_folder, filename)
                        
                        total_images += 1
                        if process_image(input_path, output_path):
                            processed_images += 1
        
        # Modo no recursivo, procesar solo la carpeta principal
        else:
            # Obtener todas las imágenes en la carpeta
            image_files = [f for f in os.listdir(input_folder) 
                          if f.lower().endswith(('.jpg', '.jpeg', '.png'))]
            
            if not image_files:
                print(f"❌ No se encontraron imágenes en la carpeta: {input_folder}")
                return 0, 0
            
            print(f"\n🔍 Procesando: {os.path.basename(input_folder)}")
            
            for filename in tqdm(image_files, desc=f"Procesando {os.path.basename(input_folder)}"):
                input_path = os.path.join(input_folder, filename)
                output_path = os.path.join(output_folder, filename)
                
                total_images += 1
                if process_image(input_path, output_path):
                    processed_images += 1
        
        return total_images, processed_images
    except Exception as e:
        print(f"❌ Error general en process_folder: {e}")
        import traceback
        traceback.print_exc()  # Imprimir el stack trace completo para mejor diagnóstico
        return 0, 0

# Menú principal
if __name__ == "__main__":
    print("===== PROCESADOR DE IMÁGENES CON YOLO =====")
    print("Este script detectará personas en las imágenes, eliminará barras negras,")
    print("recortará específicamente la región del ROSTRO sin incluir hombros")
    print("y redimensionará la imagen a 640x640 pixels.")
    print(f"Se usará el modelo YOLOv11 nano para la detección.\n")
    
    # Rutas fijas de entrada y salida - Modificar estas variables según sea necesario
    input_folder = r"C:\Users\Invitado\Documents\facial_expression_detector\data_procesada\data\SUJETO 3\señas_procesadas\A ver\muestra_1\rgb"  # Modificar esta ruta
    output_folder = r"C:\Users\Invitado\Documents\facial_expression_detector\data_procesada\data\SUJETO 3\señas_procesadas\A ver\muestra_1\cara"  # Modificar esta ruta
    
    print(f"\nProcesando imágenes...")
    print(f"Carpeta de entrada: {input_folder}")
    print(f"Carpeta de salida: {output_folder}")
    print(f"Modo recursivo: Activado\n")
    
    # Procesar las imágenes
    total, processed = process_folder(input_folder, output_folder, recursive=True)
    
    # Mostrar resultados
    print(f"\n✅ Proceso completado. {processed}/{total} imágenes procesadas")
    
    if processed < total:
        print(f"⚠️ {total - processed} imágenes no pudieron ser procesadas.")

===== PROCESADOR DE IMÁGENES CON YOLO =====
Este script detectará personas en las imágenes, eliminará barras negras,
recortará específicamente la región del ROSTRO sin incluir hombros
y redimensionará la imagen a 640x640 pixels.
Se usará el modelo YOLOv11 nano para la detección.


Procesando imágenes...
Carpeta de entrada: C:\Users\Invitado\Documents\facial_expression_detector\data_procesada\data\SUJETO 3\señas_procesadas\A ver\muestra_1\rgb
Carpeta de salida: C:\Users\Invitado\Documents\facial_expression_detector\data_procesada\data\SUJETO 3\señas_procesadas\A ver\muestra_1\cara
Modo recursivo: Activado


🔍 Procesando: .


Procesando rgb:   0%|          | 0/36 [00:00<?, ?it/s]


0: 384x640 1 person, 1 couch, 46.0ms
Speed: 1.9ms preprocess, 46.0ms inference, 0.6ms postprocess per image at shape (1, 3, 384, 640)


Procesando rgb:   3%|▎         | 1/36 [00:00<00:04,  7.64it/s]


0: 384x640 1 person, 1 couch, 40.1ms
Speed: 1.1ms preprocess, 40.1ms inference, 0.8ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 1 person, 1 couch, 47.6ms
Speed: 1.1ms preprocess, 47.6ms inference, 0.8ms postprocess per image at shape (1, 3, 384, 640)


...


0: 384x640 1 person, 1 couch, 41.4ms
Speed: 1.3ms preprocess, 41.4ms inference, 0.8ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 1 person, 1 couch, 38.6ms
Speed: 1.2ms preprocess, 38.6ms inference, 0.9ms postprocess per image at shape (1, 3, 384, 640)


Procesando rgb:  97%|█████████▋| 35/36 [00:03<00:00, 11.32it/s]


0: 384x640 1 person, 1 couch, 46.9ms
Speed: 1.2ms preprocess, 46.9ms inference, 0.8ms postprocess per image at shape (1, 3, 384, 640)


Procesando rgb: 100%|██████████| 36/36 [00:03<00:00, 10.99it/s]


✅ Proceso completado. 36/36 imágenes procesadas


ESTE RECORTA EL ROSTRO DE MANERA AUTOMATICA A TODAS LAS MUESTRAS EMPEZANDO DESDE UNA RUTA BASE, QUE DEBES DECLARAR

In [18]:
import os
import cv2
import numpy as np
from ultralytics import YOLO
from tqdm import tqdm

# Cargar el modelo YOLO11
model = YOLO('yolo11n.pt')  # Usar el modelo YOLOv11 nano

# Tamaño objetivo para normalizar
target_size = 640

def process_image(input_path, output_path):
    """
    Procesa una imagen usando YOLO para detectar personas,
    recorta la región del rostro y guarda el resultado
    """
    try:
        # Leer imagen compatible con rutas con tildes/ñ y espacios
        try:
            # Primero intentar lectura directa
            image = cv2.imread(input_path)
            
            # Si falla, usar el método alternativo con numpy
            if image is None:
                img_data = np.fromfile(input_path, dtype=np.uint8)
                image = cv2.imdecode(img_data, cv2.IMREAD_COLOR)
        except Exception as e:
            print(f"❌ Error leyendo imagen {input_path}: {e}")
            return False

        if image is None:
            print(f"❌ Imagen no leída: {input_path}")
            return False
            
        # Detectar y eliminar barras negras horizontales
        height, width = image.shape[:2]
        
        # Buscar filas completamente negras o casi negras (umbral bajo)
        threshold = 10  # Umbral para considerar un pixel como "negro"
        
        # Analizar la parte superior
        top_crop = 0
        for i in range(height // 2):  # Solo analizamos la mitad superior
            row_avg = np.mean(image[i])
            if row_avg > threshold:
                top_crop = i
                break
                
        # Analizar la parte inferior
        bottom_crop = height - 1
        for i in range(height - 1, height // 2, -1):  # Solo analizamos la mitad inferior
            row_avg = np.mean(image[i])
            if row_avg > threshold:
                bottom_crop = i
                break
                
        # Recortar la imagen para eliminar barras negras
        if top_crop > 0 or bottom_crop < height - 1:
            image = image[top_crop:bottom_crop+1, :]

        # Usar YOLO11 para detectar personas
        results = model(image)
        
        max_area = 0
        best_box = None
        
        # Iterar sobre los resultados de la detección
        for r in results:
            for box in r.boxes:
                if int(box.cls[0]) == 0:  # Clase 'persona' (generalmente 0 en YOLO)
                    x1, y1, x2, y2 = map(int, box.xyxy[0])
                    area = (x2 - x1) * (y2 - y1)  # Calcular área del bounding box
                    if area > max_area:
                        max_area = area
                        best_box = (x1, y1, x2, y2)

        # Si encontramos el bounding box con la mayor área, recortamos la imagen
        if best_box:
            x1, y1, x2, y2 = best_box
            
            # Calcular proporciones basadas en la altura total de la persona
            box_height = y2 - y1
            
            # VARIABLES QUE PUEDES MODIFICAR PARA AJUSTAR EL RECORTE FACIAL
            # -------------------------------------------------------------
            # Posición vertical del centro del rostro (ajustar entre 0.08-0.15)
            face_y_center = y1 + int(box_height * 0.1)
            
            # Altura del recorte facial (ajustar entre 0.18-0.25)
            face_height = int(box_height * 0.2)
            
            # Factor de ancho (ajustar entre 0.9-1.1)
            width_factor = 1.0
            # -------------------------------------------------------------
            
            # Calcular los puntos de recorte - asegurarnos que son enteros
            new_y1 = max(int(face_y_center - face_height/2), 0)
            new_y2 = min(int(face_y_center + face_height), image.shape[0])
            
            # Centro horizontal del rostro - usamos el centro del bounding box
            face_center_x = (x1 + x2) // 2
            
            # Calculamos márgenes laterales proporcionales a la altura
            face_width = int((new_y2 - new_y1) * width_factor)
            
            # Calculamos los límites horizontales centrados en la cara
            new_x1 = max(int(face_center_x - face_width/2), 0)
            new_x2 = min(int(face_center_x + face_width/2), image.shape[1])
            
            # Recortar la imagen en base a los nuevos límites calculados
            cropped = image[new_y1:new_y2, new_x1:new_x2]
            
            # Redimensionar directamente al tamaño objetivo
            resized = cv2.resize(cropped, (target_size, target_size), interpolation=cv2.INTER_AREA)

            # Crear directorio de salida si no existe
            os.makedirs(os.path.dirname(output_path), exist_ok=True)
            
            # Guardar la imagen procesada usando el método de codificación para manejar rutas con espacios
            try:
                # Intentar guardar directamente primero
                success = cv2.imwrite(output_path, resized)
                
                # Si falla, usar el método alternativo
                if not success:
                    _, buffer = cv2.imencode('.png', resized)
                    with open(output_path, 'wb') as f:
                        f.write(buffer)
            except Exception as e:
                print(f"❌ Error guardando la imagen {output_path}: {e}")
                return False
                
            return True
        else:
            print(f"❌ No se detectó ninguna persona en la imagen: {input_path}")
            return False
            
    except Exception as e:
        print(f"❌ Error procesando {input_path}: {e}")
        import traceback
        traceback.print_exc()  # Imprimir el stack trace completo para mejor diagnóstico
        return False

def process_folder(input_folder, output_folder):
    """
    Procesa todas las imágenes de una carpeta
    
    Args:
        input_folder: Ruta de la carpeta con las imágenes originales
        output_folder: Ruta donde guardar las imágenes procesadas
    
    Returns:
        tuple: (total_images, processed_images)
    """
    try:
        # Asegurarse de que la carpeta de salida existe
        os.makedirs(output_folder, exist_ok=True)
        
        # Obtener todas las imágenes en la carpeta
        image_files = [f for f in os.listdir(input_folder) 
                      if f.lower().endswith(('.jpg', '.jpeg', '.png'))]
        
        if not image_files:
            print(f"❌ No se encontraron imágenes en la carpeta: {input_folder}")
            return 0, 0
        
        print(f"\n🔍 Procesando: {os.path.basename(input_folder)}")
        
        total_images = 0
        processed_images = 0
        
        for filename in tqdm(image_files, desc=f"Procesando {os.path.basename(input_folder)}"):
            input_path = os.path.join(input_folder, filename)
            output_path = os.path.join(output_folder, filename)
            
            total_images += 1
            if process_image(input_path, output_path):
                processed_images += 1
        
        return total_images, processed_images
    except Exception as e:
        print(f"❌ Error general en process_folder: {e}")
        import traceback
        traceback.print_exc()  # Imprimir el stack trace completo para mejor diagnóstico
        return 0, 0

def process_all_subjects():
    """
    Procesa todos los sujetos y sus carpetas de datos
    """
    # Ruta base de los datos
    base_path = r"C:\Users\Invitado\Documents\facial_expression_detector\data_procesada\data\SUJETO 2\senas_procesadas"
    
    # Iterar sobre todos los sujetos
    for subject_dir in os.listdir(base_path):
        subject_path = os.path.join(base_path, subject_dir)
        
        # Verificar que sea un directori
        
        # Verificar que exista la carpeta de señas procesadas
            
        print(f"\n📂 Procesando sujeto: {subject_dir}")
        
        # Iterar sobre todas las carpetas de señas
        for sena_dir in os.listdir(base_path):
            sena_path = os.path.join(base_path, sena_dir)
            
            # Verificar que sea un directorio
            if not os.path.isdir(sena_path):
                continue
                
            print(f"\n📁 Procesando seña: {sena_dir}")
            
            # Buscar todas las carpetas de muestra
            for item in os.listdir(sena_path):
                if item.startswith("muestra"):
                    muestra_path = os.path.join(sena_path, item)
                    
                    # Verificar que exista la carpeta rgb
                    rgb_path = os.path.join(muestra_path, "rgb")
                    if not os.path.exists(rgb_path):
                        print(f"⚠️ No se encontró la carpeta 'rgb' para {item} en {sena_dir}")
                        continue
                        
                    # Crear la carpeta de salida (CARA)
                    cara_path = os.path.join(muestra_path, "CARA")
                    
                    # Procesar las imágenes
                    total, processed = process_folder(rgb_path, cara_path)
                    
                    print(f"✅ {item}: {processed}/{total} imágenes procesadas")

# Función principal
if __name__ == "__main__":
    print("===== PROCESADOR AUTOMÁTICO DE CARAS PARA MÚLTIPLES CARPETAS =====")
    print("Este script procesará todas las imágenes en las carpetas rgb de cada muestra")
    print("para todos los sujetos y señas, recortando el rostro y guardando en carpetas CARA.")
    print("====================================================================\n")
    
    # Procesar todos los sujetos y sus datos
    process_all_subjects()
    
    print("\n✅ Proceso completado para todos los sujetos.")

===== PROCESADOR AUTOMÁTICO DE CARAS PARA MÚLTIPLES CARPETAS =====
Este script procesará todas las imágenes en las carpetas rgb de cada muestra
para todos los sujetos y señas, recortando el rostro y guardando en carpetas CARA.


📂 Procesando sujeto: A ver

📁 Procesando seña: A ver

🔍 Procesando: rgb


Procesando rgb:   0%|          | 0/69 [00:00<?, ?it/s]


0: 384x640 1 person, 1 couch, 1 potted plant, 44.4ms
Speed: 2.4ms preprocess, 44.4ms inference, 0.6ms postprocess per image at shape (1, 3, 384, 640)


Procesando rgb:   1%|▏         | 1/69 [00:00<00:09,  7.30it/s]


0: 384x640 1 person, 1 couch, 1 potted plant, 41.8ms
Speed: 1.2ms preprocess, 41.8ms inference, 0.8ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 1 person, 1 couch, 1 potted plant, 38.9ms
Speed: 1.1ms preprocess, 38.9ms inference, 0.8ms postprocess per image at shape (1, 3, 384, 640)


...

Procesando rgb:  77%|███████▋  | 62/81 [00:05<00:01, 11.14it/s]


0: 384x640 1 person, 1 couch, 1 potted plant, 43.5ms
Speed: 1.4ms preprocess, 43.5ms inference, 0.8ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 1 person, 1 couch, 1 potted plant, 57.5ms
Speed: 1.2ms preprocess, 57.5ms inference, 1.2ms postprocess per image at shape (1, 3, 384, 640)


Procesando rgb:  79%|███████▉  | 64/81 [00:05<00:01, 10.90it/s]

Procesando rgb:  79%|███████▉  | 64/81 [00:05<00:01, 10.93it/s]


KeyboardInterrupt: 